In [8]:
%load_ext autoreload
%autoreload 2
import numpy as np
import pandas as pd
import datetime
import glob ,sys , re
from multiprocessing import Pool
import multiprocessing
from categorical_encoding import select_category_value_agg, select_level_agg, select_category_value_agg
from mv_wg_avg import exp_weight_avg

sys.path.append('../../../github/module/')
from preprocessing import set_validation, split_dataset, get_dummies, factorize_categoricals, impute_avg
from convinience_function import get_categorical_features, get_numeric_features, row_number, pararell_process
from logger import logger_func
from feature_engineering import base_aggregation, diff_feature, division_feature
from make_file import make_npy
from tqdm import tqdm

logger = logger_func()
start_time = "{0:%Y%m%d_%H%M%S}".format(datetime.datetime.now())

pd.set_option("display.max_columns", 101)
pd.set_option("display.max_rows", 101)

unique_id = 'SK_ID_CURR'
b_id = 'SK_ID'
p_id = 'SK_ID_PREV'
target = 'TARGET'
ignore_features = [unique_id, target, 'valid_no', 'is_train', 'is_test', 'SK_ID_PREV']
# dpd_ref_over_id = np.load('../data/dpd_ref_over_id.npy')

2018-08-12 17:29:04,937 logger 19 [INFO]    [logger_func] start 
2018-08-12 17:29:04,937 logger 19 [INFO]    [logger_func] start 
2018-08-12 17:29:04,937 logger 19 [INFO]    [logger_func] start 


The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [43]:
base = pd.read_csv('../data/base.csv')[unique_id].to_frame()
# app = pd.read_csv('../data/application_train_test.csv')
inst = pd.read_csv('../data/installments_payments.csv')
inst.sort_values(by=[unique_id, p_id], inplace=True)

inst['DAYS_INSTALMENT'] = (inst['DAYS_INSTALMENT']/30).astype('int')
inst['IMPUTE_ENTRY_FLG'] = inst['DAYS_ENTRY_PAYMENT'].map(lambda x: 0 if x==x else 1)
inst['IMPUTE_ENTRY_VALUE'] = inst['DAYS_INSTALMENT'] * inst['IMPUTE_ENTRY_FLG']
inst['DAYS_ENTRY_PAYMENT'] = inst['DAYS_ENTRY_PAYMENT'].fillna(0) + inst['IMPUTE_ENTRY_VALUE']
inst['DAYS_ENTRY_PAYMENT'] = (inst['DAYS_ENTRY_PAYMENT']/30).astype('int')
drop_col = [col for col in inst.columns if col.count('IMPUTE')]
inst.drop(drop_col, axis=1, inplace=True)

# 集約する
inst['INST_VERSION'] = inst['NUM_INSTALMENT_VERSION'].map(lambda x:9 if x>=8 else 6  if x==7 else x)

inst['DIFF_AMT'] = inst['AMT_INSTALMENT'] - inst['AMT_PAYMENT']
inst['DIFF_DAYS'] = inst['DAYS_INSTALMENT'] - inst['DAYS_ENTRY_PAYMENT']
inst['DIFF_DAYS'].value_counts()

# 前の行との差分
inst.sort_values(by=[unique_id, p_id, 'DAYS_INSTALMENT'], inplace=True)
inst['LAG_DAYS_INSTALMENT'] = inst.groupby([unique_id, p_id])['DAYS_INSTALMENT'].shift(-1)
inst.sort_values(by=[unique_id, p_id, 'DAYS_ENTRY_PAYMENT'], inplace=True)
inst['LAG_DAYS_ENTRY'] = inst.groupby([unique_id, p_id])['DAYS_ENTRY_PAYMENT'].shift(-1)
inst['DIFF_DAYS_INSTALMENT'] = inst['LAG_DAYS_INSTALMENT'] - inst['DAYS_INSTALMENT']
inst['DIFF_DAYS_ENTRY'] = inst['LAG_DAYS_ENTRY'] - inst['DAYS_ENTRY_PAYMENT']

drop_col = [col for col in inst.columns if col.count('LAG_')]
inst.drop(drop_col, axis=1, inplace=True)

In [44]:
# win = pd.read_csv('../data/application_summary_set.csv')
# prev = pd.read_csv('../data/previous_cleansing.csv')
prev['CNT_ANNUITY'] = prev['AMT_CREDIT'] / prev['AMT_ANNUITY']
prev = prev[[unique_id, p_id, 'AMT_CREDIT', 'AMT_ANNUITY', 'CNT_ANNUITY', 'DAYS_LAST_DUE_1ST_VERSION']]
inst = inst.merge(prev, on=[unique_id, p_id], how='inner')

In [96]:
' 残期間を差、割合の2パターンで '
inst['REMAING_PERIOD_DIFF@'] = inst['DAYS_LAST_DUE_1ST_VERSION'] - inst['DAYS_INSTALMENT']
inst['REMAING_PERIOD_RATIO@'] = inst['DAYS_INSTALMENT'] / inst['DAYS_LAST_DUE_1ST_VERSION']

inst['INS_CNT_ANNUITY@'] = inst['AMT_CREDIT'] / inst['AMT_INSTALMENT']
inst['CNT_ANNUITY_diff_INS_CNT_ANNUITY@'] = inst['CNT_ANNUITY'] - inst['INS_CNT_ANNUITY@']

' 分割数の最頻値をとってカラムにする→CNT_ANNUITYと同じように特徴を作っていく。どっちが効くか？ '
inst_cnt_mode = inst.groupby([unique_id, p_id])['INS_CNT_ANNUITY@'].median().reset_index()
inst.drop('INS_CNT_ANNUITY@', axis=1, inplace=True)
inst = inst.merge(inst_cnt_mode, on=[unique_id, p_id], how='inner')

' 残回数を出す。2パターン。効く方を残す予定。純粋な特徴を作る時はprev_idでminをとる '
inst['REMAING_INS_CNT_INSTALMENT_DIFF@'] = inst['INS_CNT_ANNUITY@'] - inst['NUM_INSTALMENT_NUMBER']
inst['REMAING_INS_CNT_INSTALMENT_RATIO@'] = inst['NUM_INSTALMENT_NUMBER'] / inst['INS_CNT_ANNUITY@']
inst['REMAING_CNT_INSTALMENT_DIFF@'] = inst['CNT_ANNUITY'] - inst['NUM_INSTALMENT_NUMBER']
inst['REMAING_CNT_INSTALMENT_RATIO@'] = inst['NUM_INSTALMENT_NUMBER'] / inst['CNT_ANNUITY']

inst = inst.merge(app[[unique_id, 'AMT_INCOME_TOTAL']], on=unique_id, how='inner')

inst['REMAING_AMT_INSTALMENT@'] = inst['REMAING_CNT_INSTALMENT_DIFF@'] * inst['AMT_ANNUITY']
inst['REMAING_INS_AMT_INSTALMENT@'] =inst['REMAING_INS_CNT_INSTALMENT_DIFF@'] * inst['AMT_ANNUITY']
inst['REMAING_AMT_INSTALMENT@_div_INCOME@']     = inst['REMAING_AMT_INSTALMENT@']     / inst['AMT_INCOME_TOTAL']
inst['REMAING_INS_AMT_INSTALMENT@_div_INCOME@'] = inst['REMAING_INS_AMT_INSTALMENT@'] / inst['AMT_INCOME_TOTAL']

In [98]:
inst.head()

SK_ID_PREV  SK_ID_CURR  NUM_INSTALMENT_VERSION  NUM_INSTALMENT_NUMBER  \
0     1369693      100001                     1.0                      1   
1     1369693      100001                     1.0                      2   
2     1369693      100001                     1.0                      3   
3     1369693      100001                     2.0                      4   
4     1038818      100002                     1.0                      1   

   DAYS_INSTALMENT  DAYS_ENTRY_PAYMENT  AMT_INSTALMENT  AMT_PAYMENT  TARGET  \
0              -56                 -57        3951.000     3951.000      -1   
1              -55                 -57        3951.000     3951.000      -1   
2              -54                 -55        3951.000     3951.000      -1   
3              -53                 -54       17397.900    17397.900      -1   
4              -18                 -19        9251.775     9251.775       1   

   INST_VERSION  DIFF_AMT  DIFF_DAYS  DIFF_DAYS_INSTALMENT  DIFF_DAYS_ENTRY  \
0           1.0       0.0          1                   1.0              0.0   
1           1.0       0.0          2                   1.0              2.0   
2           1.0       0.0          1                   1.0              1.0   
3           2.0       0.0          1                   NaN              NaN   
4           1.0       0.0          1                   1.0              1.0   

   AMT_CREDIT  AMT_ANNUITY  CNT_ANNUITY  DAYS_LAST_DUE_1ST_VERSION  \
0     23787.0     3951.000     6.020501                      -49.0   
1     23787.0     3951.000     6.020501                      -49.0   
2     23787.0     3951.000     6.020501                      -49.0   
3     23787.0     3951.000     6.020501                      -49.0   
4    179055.0     9251.775    19.353584                        4.0   

   REMAING_PERIOD_DIFF  REMAING_PERIOD_RATIO  \
0                  7.0              1.142857   
1                  6.0              1.122449   
2                  5.0              1.102041   
3                  4.0              1.081633   
4                 22.0             -4.500000   

   CNT_ANNUITY_diff_INS_CNT_ANNUITY  INS_CNT_ANNUITY  \
0                          0.000000         6.020501   
1                          0.000000         6.020501   
2                          0.000000         6.020501   
3                          4.653267         6.020501   
4                          0.000000        19.353584   

   REMAING_INS_CNT_INSTALMENT_DIFF  REMAING_INS_CNT_INSTALMENT_RATIO  \
0                         5.020501                          0.166099   
1                         4.020501                          0.332198   
2                         3.020501                          0.498297   
3                         2.020501                          0.664397   
4                        18.353584                          0.051670   

   REMAING_CNT_INSTALMENT_DIFF  REMAING_CNT_INSTALMENT_RATIO  \
0                     5.020501                      0.166099   
1                     4.020501                      0.332198   
2                     3.020501                      0.498297   
3                     2.020501                      0.664397   
4                    18.353584                      0.051670   

   REMAING_PERIOD_DIFF@  REMAING_PERIOD_RATIO@  \
0                   7.0               1.142857   
1                   6.0               1.122449   
2                   5.0               1.102041   
3                   4.0               1.081633   
4                  22.0              -4.500000   

   CNT_ANNUITY_diff_INS_CNT_ANNUITY@  INS_CNT_ANNUITY@  \
0                           0.000000          6.020501   
1                           0.000000          6.020501   
2                           0.000000          6.020501   
3                           4.653267          6.020501   
4                           0.000000         19.353584   

   REMAING_INS_CNT_INSTALMENT_DIFF@  REMAING_INS_CNT_INSTALMENT_RATIO@  \
0      

In [79]:
' 遅延が発生したタイミングに関するfeatureを作成する '
inst_diff = inst.query('DIFF_AMT != 0')
diff_min = inst_diff.groupby([unique_id, p_id])['NUM_INSTALMENT_NUMBER'].min()
diff_max = inst_diff.groupby([unique_id, p_id])['NUM_INSTALMENT_NUMBER'].max()
diff_std = inst_diff.groupby([unique_id, p_id])['NUM_INSTALMENT_NUMBER'].std()
diff_min= diff_min.reset_index().rename(columns={'NUM_INSTALMENT_NUMBER':'DIFF_INSTALMENT_NUMBER_min'})
diff_max= diff_max.reset_index().rename(columns={'NUM_INSTALMENT_NUMBER':'DIFF_INSTALMENT_NUMBER_max'})
diff_std= diff_std.reset_index().rename(columns={'NUM_INSTALMENT_NUMBER':'DIFF_INSTALMENT_NUMBER_std'})

result_diff = inst_diff.merge(diff_min, on=[unique_id, p_id], how='inner').merge(diff_max, on=[unique_id, p_id], how='inner').merge(diff_std, on=[unique_id, p_id], how='inner')

result_diff['DEF_PAYMENT_DIFF'] = result_diff['DIFF_INSTALMENT_NUMBER_min'] - result_diff['CNT_ANNUITY']
result_diff['DEF_PAYMENT_RATIO']= result_diff['DIFF_INSTALMENT_NUMBER_min'] / result_diff['CNT_ANNUITY']
result_diff['DEF_INS_PAYMENT_DIFF'] = result_diff['DIFF_INSTALMENT_NUMBER_min'] - result_diff['INS_CNT_ANNUITY']
result_diff['DEF_INS_PAYMENT_RATIO']= result_diff['DIFF_INSTALMENT_NUMBER_min'] / result_diff['INS_CNT_ANNUITY']

column_list = [unique_id, p_id] + [col for col in result_diff.columns if (col.count('DEF') or col.count('DIFF_') or col.count('DAYS')) and not(col.count('AMT'))]
result_diff = result_diff[column_list].drop_duplicates()
for col in result_diff.columns:
    if col not in ignore_features:
        result_diff.rename(columns={col:f'{col}@'}, inplace=True)
        
result_diff['DIFF_INSTALMENT_NUMBER_MAX_TERM@'] = result_diff['DIFF_INSTALMENT_NUMBER_max@'] - result_diff['DIFF_INSTALMENT_NUMBER_min@']

result_diff = result_diff.groupby([unique_id, p_id]).max().reset_index()

drop_list = ['DIFF_DAYS@', 'DIFF_DAYS_INSTALMENT@']
result_diff.drop(drop_list, axis=1, inplace=True)

In [18]:
win_list = [unique_id, 'a_DAYS_REGISTRATION', 'a_DAYS_EMPLOYED_impute', 'a_DAYS_ID_PUBLISH', 'a_DAYS_LAST_PHONE_CHANGE_impute', 'a_REGION_POPULATION_RELATIVE']
win = win[win_list]

for num in win_list:
    if num in ignore_features:
        continue
    birth = win[num].values
    birth = birth - birth.min() +1
    birth = np.log10(birth)
    win[f'{num}_log10'] = birth
    win.drop(num, axis=1, inplace=True)
inst = inst.merge(win, on=unique_id, how='inner')

inst_amt = ['AMT_INSTALMENT', 'AMT_PAYMENT', 'DIFF_AMT']
log_list = [col for col in win.columns if col.count('log10')]

for amt in inst_amt:
    for log in log_list:
        inst = division_feature(df=inst, first=amt, second=log)
for log in log_list:    
    inst.drop(log, axis=1, inplace=True)
print(inst.columns)

Index(['SK_ID_PREV', 'SK_ID_CURR', 'NUM_INSTALMENT_VERSION',
       'NUM_INSTALMENT_NUMBER', 'DAYS_INSTALMENT', 'DAYS_ENTRY_PAYMENT',
       'AMT_INSTALMENT', 'AMT_PAYMENT', 'TARGET', 'INST_VERSION', 'DIFF_AMT',
       'DIFF_DAYS', 'DIFF_DAYS_INSTALMENT', 'DIFF_DAYS_ENTRY',
       'AMT_INSTALMENT_div_a_DAYS_REGISTRATION_log10@',
       'AMT_INSTALMENT_div_a_DAYS_EMPLOYED_impute_log10@',
       'AMT_INSTALMENT_div_a_DAYS_ID_PUBLISH_log10@',
       'AMT_INSTALMENT_div_a_DAYS_LAST_PHONE_CHANGE_impute_log10@',
       'AMT_INSTALMENT_div_a_REGION_POPULATION_RELATIVE_log10@',
       'AMT_PAYMENT_div_a_DAYS_REGISTRATION_log10@',
       'AMT_PAYMENT_div_a_DAYS_EMPLOYED_impute_log10@',
       'AMT_PAYMENT_div_a_DAYS_ID_PUBLISH_log10@',
       'AMT_PAYMENT_div_a_DAYS_LAST_PHONE_CHANGE_impute_log10@',
       'AMT_PAYMENT_div_a_REGION_POPULATION_RELATIVE_log10@',
       'a_DAYS_REGISTRATION_log10_div_DIFF_AMT@',
       'a_DAYS_EMPLOYED_impute_log10_div_DIFF_AMT@',
       'a_DAYS_ID_PUBLISH_log10_d

In [3]:
' 延滞or拒否を経験したことのあるID '
' インデックスにSK_ID_CURRをセットしないとだめだめよ '
dpd_index = pd.Series(dpd_ref_over_id, name='SK_ID_CURR').to_frame()
inst_dpd = inst.merge(dpd_index, on=unique_id, how='inner')

In [5]:
amt_list = [col for col in inst.columns if col.count('AMT')]
days_list = [col for col in inst.columns if col.count('DAYS')]
other_list = ['NUM_INSTALMENT_VERSION', 'NUM_INSTALMENT_NUMBER']
div_list = [col for col in inst.columns if col.count('@')]
all_list = amt_list + days_list + other_list + div_list

In [106]:
# inst.sort_values(by=[unique_id, 'DAYS_INSTALMENT'], ascending=True, inplace=True)
# inst = row_number(inst, unique_id)
inst.head()

SK_ID_PREV  SK_ID_CURR  NUM_INSTALMENT_VERSION  NUM_INSTALMENT_NUMBER  \
0     1369693      100001                     1.0                      1   
1     1369693      100001                     1.0                      2   
2     1369693      100001                     1.0                      3   
3     1369693      100001                     2.0                      4   
4     1038818      100002                     1.0                      1   

   DAYS_INSTALMENT  DAYS_ENTRY_PAYMENT  AMT_INSTALMENT  AMT_PAYMENT  TARGET  \
0              -56                 -57        3951.000     3951.000      -1   
1              -55                 -57        3951.000     3951.000      -1   
2              -54                 -55        3951.000     3951.000      -1   
3              -53                 -54       17397.900    17397.900      -1   
4              -18                 -19        9251.775     9251.775       1   

   INST_VERSION  DIFF_AMT  DIFF_DAYS  DIFF_DAYS_INSTALMENT  DIFF_DAYS_ENTRY  \
0           1.0       0.0          1                   1.0              0.0   
1           1.0       0.0          2                   1.0              2.0   
2           1.0       0.0          1                   1.0              1.0   
3           2.0       0.0          1                   NaN              NaN   
4           1.0       0.0          1                   1.0              1.0   

   AMT_CREDIT  AMT_ANNUITY  CNT_ANNUITY  DAYS_LAST_DUE_1ST_VERSION  \
0     23787.0     3951.000     6.020501                      -49.0   
1     23787.0     3951.000     6.020501                      -49.0   
2     23787.0     3951.000     6.020501                      -49.0   
3     23787.0     3951.000     6.020501                      -49.0   
4    179055.0     9251.775    19.353584                        4.0   

   REMAING_PERIOD_DIFF  REMAING_PERIOD_RATIO  \
0                  7.0              1.142857   
1                  6.0              1.122449   
2                  5.0              1.102041   
3                  4.0              1.081633   
4                 22.0             -4.500000   

   CNT_ANNUITY_diff_INS_CNT_ANNUITY  INS_CNT_ANNUITY  \
0                          0.000000         6.020501   
1                          0.000000         6.020501   
2                          0.000000         6.020501   
3                          4.653267         6.020501   
4                          0.000000        19.353584   

   REMAING_INS_CNT_INSTALMENT_DIFF  REMAING_INS_CNT_INSTALMENT_RATIO  \
0                         5.020501                          0.166099   
1                         4.020501                          0.332198   
2                         3.020501                          0.498297   
3                         2.020501                          0.664397   
4                        18.353584                          0.051670   

   REMAING_CNT_INSTALMENT_DIFF  REMAING_CNT_INSTALMENT_RATIO  \
0                     5.020501                      0.166099   
1                     4.020501                      0.332198   
2                     3.020501                      0.498297   
3                     2.020501                      0.664397   
4                    18.353584                      0.051670   

   REMAING_PERIOD_DIFF@  REMAING_PERIOD_RATIO@  \
0                   7.0               1.142857   
1                   6.0               1.122449   
2                   5.0               1.102041   
3                   4.0               1.081633   
4                  22.0              -4.500000   

   CNT_ANNUITY_diff_INS_CNT_ANNUITY@  INS_CNT_ANNUITY@  \
0                           0.000000          6.020501   
1                           0.000000          6.020501   
2                           0.000000          6.020501   
3                           4.653267          6.020501   
4                           0.000000         19.353584   

   REMAING_INS_CNT_INSTALMENT_DIFF@  REMAING_INS_CNT_INSTALMENT_RATIO@  \
0      

In [108]:
drop_list = ['diff', 'weight', 'tmp']
inst.drop(drop_list, axis=1, inplace=True)
inst.to_csv('../data/installment_feature_table.csv', index=False)
# inst

OSError: [Errno 12] Cannot allocate memory

In [20]:
time_col = 'DAYS_INSTALMENT'
' 時系列で区切る '
# year = inst.query(f"{time_col}>=-1")
' 回数で区切る '
lateset_cnt = inst.query(f"row_no<=12")
df = lateset_cnt
prefix = 'is_latest12_'
print(df.shape)

(3726734, 30)


In [99]:
# data = df
prefix = 'is_rm_'
data = inst
num_list = [col for col in data.columns if col.count('@')]
# cat_list = ['INST_VERSION']

# select_category_value_agg(base=base, data=data, cat_list=cat_list, ignore_list=ignore_features, level=unique_id, method_list=method_list, num_list=num_list, prefix=prefix)

In [100]:
' 1段階の集計 '
# data = df
data = inst
level = unique_id
num_list = [col for col in data.columns if col.count('@')]
method_list = ['sum', 'mean', 'std', 'max', 'min']

select_level_agg(base=base, data=data, ignore_list=ignore_features,  level=level, method_list=method_list, num_list=num_list, prefix=prefix)

2018-08-12 21:53:34,721 logger 231 [INFO]    [select_level_agg] 
num: REMAING_PERIOD_DIFF@
method: sum
['SK_ID_CURR'] 
2018-08-12 21:53:34,721 logger 231 [INFO]    [select_level_agg] 
num: REMAING_PERIOD_DIFF@
method: sum
['SK_ID_CURR'] 
2018-08-12 21:53:34,721 logger 231 [INFO]    [select_level_agg] 
num: REMAING_PERIOD_DIFF@
method: sum
['SK_ID_CURR'] 
../../../github/module/feature_engineering.py:26: FutureWarning: using a dict on a Series for aggregation
is deprecated and will be removed in a future version
  result = df.groupby(level)[feature].agg({'tmp': {method}})
2018-08-12 21:53:49,860 logger 236 [INFO]    [select_level_agg] 
base: Index(['SK_ID_CURR'], dtype='object')
result: Index(['SK_ID_CURR', 'REMAING_PERIOD_DIFF@_sum@['SK_ID_CURR']'], dtype='object') 
2018-08-12 21:53:49,860 logger 236 [INFO]    [select_level_agg] 
base: Index(['SK_ID_CURR'], dtype='object')
result: Index(['SK_ID_CURR', 'REMAING_PERIOD_DIFF@_sum@['SK_ID_CURR']'], dtype='object') 
2018-08-12 21:53:49,860 

2018-08-12 21:53:51,048 logger 29 [INFO]    [make_npy] 5.500000     13884
2.500000     12438
4.500000     11064
6.000000      6353
5.000000      5939
8.500000      4416
6.500000      4242
3.000000      3525
3.500000      3417
4.000000      3246
7.000000      3083
7.500000      2593
8.000000      2537
9.500000      2489
9.000000      2341
11.500000     1909
1.500000      1900
10.000000     1620
2.000000      1526
12.000000     1185
11.000000     1138
3.750000      1049
5.045455       930
13.000000      841
14.000000      820
12.500000      818
15.000000      760
10.500000      748
14.500000      728
13.500000      710
17.000000      692
16.000000      680
4.764706       673
4.666667       660
17.500000      654
15.500000      628
5.285714       616
5.333333       597
18.000000      586
2.142857       558
16.500000      543
5.666667       526
2.727273       519
4.900000       502
5.076923       492
5.153846       473
18.500000      447
4.090909       447
19.000000      438
2.285714      

2018-08-12 21:53:52,375 logger 29 [INFO]    [make_npy] 1.870829     14384
3.027650     10489
3.605551     10333
1.290994      7198
1.581139      6635
2.738613      5457
2.449490      5108
3.316625      4851
2.160247      3656
1.000000      3033
5.338539      1430
3.399827      1283
7.071068      1232
4.183300      1126
0.707107      1040
1.783765       999
2.768875       970
4.760952       967
5.049752       950
3.316298       921
3.894440       905
4.472136       887
3.526299       804
3.307745       659
6.782330       632
1.951800       623
1.799471       572
3.670744       560
1.663330       553
6.493587       483
1.678744       477
2.946898       472
2.672612       467
3.176619       462
3.400767       460
5.627314       447
3.774068       434
5.916080       428
6.204837       423
3.195980       404
3.454837       399
3.265986       385
3.060006       385
3.614784       326
2.876235       324
1.678744       305
3.415650       298
2.951066       285
3.278318       263
1.140175      

2018-08-12 21:53:54,415 logger 29 [INFO]    [make_npy]  0.0     220626
 1.0      34162
 2.0      17967
 3.0      11747
 4.0       8356
 5.0       6962
 6.0       6540
 7.0       5018
 8.0       4458
 9.0       2757
 10.0      1916
 11.0      1548
 12.0      1209
-1.0       1125
 13.0      1109
 14.0      1008
 15.0       838
 16.0       748
 17.0       645
 18.0       509
 19.0       464
 20.0       404
 21.0       332
 22.0       305
 38.0       280
 26.0       238
 23.0       227
 27.0       213
 25.0       210
 24.0       209
 29.0       206
 28.0       195
 31.0       176
 30.0       175
 32.0       143
 33.0       121
 34.0       110
 39.0       110
 40.0        73
 41.0        72
 35.0        71
 37.0        69
 42.0        65
 44.0        61
 43.0        58
 36.0        54
 45.0        42
 47.0        30
 46.0        29
-2.0         24
 48.0        14
 49.0        14
 50.0        11
 52.0         9
 53.0         7
 54.0         6
 51.0         6
 55.0         4
 57.0         3
 

2018-08-12 21:53:55,369 logger 231 [INFO]    [select_level_agg] 
num: REMAING_PERIOD_RATIO@
method: mean
['SK_ID_CURR'] 
2018-08-12 21:53:55,369 logger 231 [INFO]    [select_level_agg] 
num: REMAING_PERIOD_RATIO@
method: mean
['SK_ID_CURR'] 
2018-08-12 21:53:55,369 logger 231 [INFO]    [select_level_agg] 
num: REMAING_PERIOD_RATIO@
method: mean
['SK_ID_CURR'] 
2018-08-12 21:53:56,158 logger 236 [INFO]    [select_level_agg] 
base: Index(['SK_ID_CURR'], dtype='object')
result: Index(['SK_ID_CURR', 'REMAING_PERIOD_RATIO@_mean@['SK_ID_CURR']'], dtype='object') 
2018-08-12 21:53:56,158 logger 236 [INFO]    [select_level_agg] 
base: Index(['SK_ID_CURR'], dtype='object')
result: Index(['SK_ID_CURR', 'REMAING_PERIOD_RATIO@_mean@['SK_ID_CURR']'], dtype='object') 
2018-08-12 21:53:56,158 logger 236 [INFO]    [select_level_agg] 
base: Index(['SK_ID_CURR'], dtype='object')
result: Index(['SK_ID_CURR', 'REMAING_PERIOD_RATIO@_mean@['SK_ID_CURR']'], dtype='object') 
2018-08-12 21:53:56,286 logger 239

...

2018-08-12 21:54:53,778 logger 29 [INFO]    [make_npy]  0.000000     328
-2.000000     286
-1.500000     283
-3.000000     276
-1.000000     257
-2.500000     196
-0.500000     194
-1.200000     193
-1.800000     191
-0.600000     183
-0.200000     176
-2.400000     175
-4.000000     173
-2.250000     156
-0.400000     156
-0.100000     155
-0.300000     154
-1.400000     151
-0.800000     149
-5.000000     143
-0.250000     138
-1.600000     137
-0.900000     136
-1.250000     133
-2.100000     132
-3.600000     130
-3.400000     126
-0.750000     125
-1.700000     123
-3.500000     123
-2.200000     122
-1.666667     120
-1.750000     119
-4.500000     112
-0.150000     111
-2.600000     110
-2.800000     109
 0.100000     107
-1.333333     106
-3.750000     105
-4.800000     103
-6.000000     103
-1.300000     101
-4.200000      99
-3.200000      99
-2.700000      98
-0.666667      97
-0.050000      96
-3.800000      94
-2.666667      94
             ... 
-0.004876       1
-0.216801

2018-08-12 21:54:54,762 logger 29 [INFO]    [make_npy]  inf            11
 2.923986        8
 0.000000        6
 2.500000        6
 5.035677        5
 4.500000        5
 0.449772        4
 3.000000        4
 2.416667        4
 4.050000        4
 0.810690        4
 4.725000        4
 3.356973        4
 3.655002        4
 0.870810        4
 2.774206        4
 3.150000        4
 1.635544        3
 7.263765        3
 2.250761        3
 3.508783        3
 0.089173        3
 4.200660        3
 3.341940        3
 5.847972        3
 0.336492        3
 0.719635        3
 1.849458        3
 2.994852        3
 2.026725        3
 3.080000        3
 2.281620        3
-104.400000      3
 2.480000        3
 0.675575        3
 4.600000        3
 4.873336        3
 4.861111        3
 4.438730        3
 3.376142        3
 0.242984        3
 0.648724        3
 1.199342        3
 1.928571        3
 3.817715        3
 3.500000        3
 0.230200        3
 2.700000        3
 2.069386        3
 2.833333     

2018-08-12 21:54:55,863 logger 29 [INFO]    [make_npy]  inf           11
 0.243666       8
 0.250000       6
 0.419640       5
 0.178571       5
 0.231184       4
 0.074962       4
 0.145135       4
 0.500000       4
 0.125000       4
 0.225000       4
 0.135115       4
 0.241667       4
 0.304583       4
 0.279748       4
 0.417743       3
 0.450000       3
 0.217302       3
 0.204615       3
 0.200000       3
 0.200000       3
 0.040497       3
 0.069195       3
 0.290247       3
 0.022293       3
 0.112596       3
 0.134163       3
 0.119934       3
 0.056082       3
 0.487331       3
 0.214286       3
 0.149924       3
 0.119939       3
 0.322996       3
 0.369894       3
 0.310000       3
 0.253513       3
 0.393290       3
 0.406111       3
 0.272591       3
 0.108121       3
 0.043103       3
 0.147900       3
-1.200000       3
 0.344898       3
 0.292399       3
 0.287500       3
-1.000000       3
 0.420066       3
 0.280000       3
               ..
 0.371548       1
 0.268693

2018-08-12 21:54:56,977 logger 231 [INFO]    [select_level_agg] 
num: REMAING_INS_AMT_INSTALMENT@_div_INCOME@
method: max
['SK_ID_CURR'] 
2018-08-12 21:54:56,977 logger 231 [INFO]    [select_level_agg] 
num: REMAING_INS_AMT_INSTALMENT@_div_INCOME@
method: max
['SK_ID_CURR'] 
2018-08-12 21:54:56,977 logger 231 [INFO]    [select_level_agg] 
num: REMAING_INS_AMT_INSTALMENT@_div_INCOME@
method: max
['SK_ID_CURR'] 
2018-08-12 21:54:58,002 logger 236 [INFO]    [select_level_agg] 
base: Index(['SK_ID_CURR'], dtype='object')
result: Index(['SK_ID_CURR', 'REMAING_INS_AMT_INSTALMENT@_div_INCOME@_max@['SK_ID_CURR']'], dtype='object') 
2018-08-12 21:54:58,002 logger 236 [INFO]    [select_level_agg] 
base: Index(['SK_ID_CURR'], dtype='object')
result: Index(['SK_ID_CURR', 'REMAING_INS_AMT_INSTALMENT@_div_INCOME@_max@['SK_ID_CURR']'], dtype='object') 
2018-08-12 21:54:58,002 logger 236 [INFO]    [select_level_agg] 
base: Index(['SK_ID_CURR'], dtype='object')
result: Index(['SK_ID_CURR', 'REMAING_INS

2018-08-12 21:54:59,511 logger 239 [INFO]    [select_level_agg] 
result shape: (356255, 2) 
2018-08-12 21:54:59,511 logger 239 [INFO]    [select_level_agg] 
result shape: (356255, 2) 
2018-08-12 21:54:59,511 logger 239 [INFO]    [select_level_agg] 
result shape: (356255, 2) 
2018-08-12 21:54:59,565 logger 29 [INFO]    [make_npy]  0.000000    100
-1.800000     49
-2.000000     44
-3.000000     43
-0.100000     43
-2.400000     41
-3.600000     38
-0.166468     36
-2.250000     35
 0.100000     35
-1.500000     34
-2.800000     32
-2.700000     32
-2.100000     31
-0.200000     31
-0.221957     31
-3.200000     30
-0.380648     30
-0.244796     29
-5.000000     29
-4.000000     29
-1.200000     28
-2.200000     28
-1.000000     28
-1.600000     27
-2.500000     26
-0.300000     26
-3.750000     26
-3.900000     26
-0.266349     26
-4.800000     26
-4.200000     25
-0.190324     25
-3.400000     25
-0.750000     25
-3.800000     24
-0.050000     24
-1.400000     24
-2.666667     24
-1.750

In [101]:
' 1段階の重み付き平均 '
# data = df
data = inst
level = unique_id
label = 'DAYS_INSTALMENT'
# label = 'DAYS_INSTALMENT@'
weight_list = [0.97]
num_list = [col for col in data.columns if col.count('@')]

for num in num_list:
    for weight in weight_list:
        wavg = exp_weight_avg(data=data, level=level, weight=weight, label=label, value=num)
        result = base.merge(wavg.to_frame().reset_index(), on=unique_id, how='left').fillna(0)
        make_npy(logger=logger, result=result, ignore_list=ignore_features, prefix=prefix)

/mnt/c/Git/go/kaggle/kaggle_private/home-credit-default-risk/engineering/mv_wg_avg.py:85: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  null['weight'] = 0
2018-08-12 21:56:17,195 logger 29 [INFO]    [make_npy] 0.000000     22162
2.411211      6355
5.137839      3951
5.137839      3803
4.249103      3461
4.249103      3189
2.411211      2473
2.411211      2466
5.137839      1400
8.411211      1231
2.939106      1189
5.249103      1099
4.797196       998
5.695981       977
5.695981       965
4.695981       897
2.939106       884
5.137839       860
5.695981       843
1.461936       820
9.461936       803
5.797196       795
1.461936       774
3.461936       769
8.461936       757
6.340250       729
4.797196       709
6.249103       673
1.939106       583
6.878257    

2018-08-12 21:57:25,215 logger 29 [INFO]    [make_npy] -inf         34919
 0.000000    22374
-4.249103      832
-1.898598      795
-1.113417      674
 6.137839      479
-0.719564      458
 1.482242      424
-3.340250      394
 2.712613      387
 1.803737      373
 3.568920      371
 1.602803      363
 1.301401      362
 2.027568      352
 2.205606      340
 2.284460      336
 1.267912      331
 1.200934      328
 1.401869      325
 1.344459      321
 1.241121      306
 3.411211      304
-1.439129      298
-0.323184      293
 5.249103      292
 1.642230      289
-1.461936      288
 1.219201      283
 1.856307      278
-0.482242      272
 1.733977      272
 2.416368      250
 1.185478      248
 1.172229      246
-0.208848      238
 1.160747      237
 1.570871      236
-0.667393      234
 1.467076      233
-0.804176      233
 1.141836      227
-1.212039      226
-0.391332      225
-0.467076      224
 2.062276      222
-0.979329      221
-0.326854      220
-0.557469      219
 1.513784     

2018-08-12 21:58:31,648 logger 29 [INFO]    [make_npy]  0.000000e+00    36188
-inf                36
-7.490211e-04        7
-2.283947e-04        7
-2.283947e-04        7
-2.255743e-04        6
-2.703848e-04        6
-7.490211e-04        6
-7.490211e-04        6
-2.808122e-04        6
-2.578444e-04        6
-7.381244e-04        6
-2.285621e-03        5
-2.177588e-04        5
-7.187398e-04        5
-7.187398e-04        5
-7.311063e-04        5
-2.221989e-04        5
-2.720916e-04        5
 1.411828e+00        5
-2.019941e-04        5
 3.987236e+00        4
-1.146711e-03        4
-6.967234e-04        4
-2.106619e-04        4
-2.494174e-04        4
-6.558720e-03        4
 7.664440e-01        4
-1.488356e-04        4
-2.135888e-04        4
 1.411828e+00        4
-7.198209e-04        4
-7.577386e-04        4
-2.025467e-04        4
-7.198209e-04        4
 2.394194e-01        4
-2.202557e-04        4
 1.085163e+00        4
 2.218632e+00        4
 1.730238e+00        4
-2.177588e-04        4
-7

2018-08-12 22:01:14,623 logger 29 [INFO]    [make_npy]  0.000000     19324
 3.340012       115
 3.340012        65
 3.340012        60
 3.340012        60
 3.340012        60
 2.944755        56
 3.340012        55
 3.888105        42
 3.888105        41
 2.582436        38
 4.431159        38
 3.888105        38
 4.431159        37
 3.851359        37
 3.137839        31
 3.340012        30
 3.137839        30
 4.409501        29
 4.969166        26
 3.250003        24
 4.431159        24
 3.137839        23
 6.165406        22
 1.342666        22
 3.888105        21
 5.502121        19
 2.582436        19
 2.582436        17
 3.492848        16
 1.342658        15
 2.071482        15
 2.944755        14
 3.851359        14
 1.563851        14
 6.053770        14
 6.165406        13
 3.250003        13
 1.563851        13
 2.281931        13
 2.582436        12
 3.673583        12
 3.250003        12
 5.502121        12
 2.582436        12
 4.962624        12
 6.552845        12
 4.03

2018-08-12 22:02:49,280 logger 29 [INFO]    [make_npy] 0.000000    19325
0.632599      162
0.632599      153
0.632599      114
0.572308       95
0.572308       55
0.690108       54
0.512573       46
0.512573       46
0.661353       45
0.686216       44
0.686216       42
0.640514       33
0.690108       33
0.638925       29
0.661353       29
0.634031       28
0.588417       27
0.638925       26
0.814402       23
0.453392       23
0.632599       22
0.814402       22
0.512573       21
0.453392       21
0.367923       21
0.624337       18
0.727734       18
0.536789       17
0.686216       17
0.640514       16
0.727735       15
0.394767       15
0.572308       15
0.814401       15
0.367923       14
0.598323       14
0.559170       14
0.727735       14
0.394767       14
0.690108       14
0.572308       13
0.748162       13
0.750447       13
0.640240       13
0.659897       13
0.336698       13
0.652011       13
0.640514       12
0.646976       11
            ...  
0.448984        1
0.883441 

2018-08-12 22:04:17,839 logger 29 [INFO]    [make_npy]  0.000000     19324
 3.340012       111
 3.340012        60
 3.340012        59
 3.340012        59
 3.340012        58
 2.944755        55
 3.340012        53
 3.888105        41
 3.888105        40
 3.888105        38
 2.582436        37
 4.431159        37
 4.431159        35
 3.851359        34
 3.137839        31
 3.340012        29
 3.137839        28
 4.409501        27
 4.969166        25
 4.431159        24
 3.137839        23
 1.342666        22
 3.250003        21
 3.888105        21
 2.582436        19
 5.502121        19
 6.165406        19
 2.582436        17
 1.342658        15
 3.492848        15
 1.563851        14
 2.944755        14
 3.851359        14
 13.388548       14
 6.053770        13
 1.563851        13
 2.281931        13
 5.502121        12
 3.673583        12
 3.250003        12
 2.582436        12
 6.552845        12
 19.000000       12
 2.582436        12
 6.693300        11
 4.969166        11
 4.96

2018-08-12 22:06:37,300 logger 29 [INFO]    [make_npy]  0.000000         19324
 601774.948846       15
 724948.500491       10
 71119.756089        10
 676358.033883       10
 12656.217642        10
 3861.530594         10
 601774.948846        9
 12656.217642         9
 651722.925409        9
 283348.693593        9
 748903.186089        8
 3738.225129          7
 525165.780084        7
 865261.440000        7
 44515.979952         7
 40801.813499         7
 796130.092569        6
 819401.891304        6
 700766.677907        6
 472974.730875        6
 446545.641918        6
 772630.460803        6
 338622.675550        6
 419895.118986        6
 393023.916318        6
 283348.693593        6
 26709.402693         6
 23942.069706         5
 311094.331213        5
 26709.402693         5
 12656.217642         5
 42883.290431         5
 18121.167758         5
 73619.453788         5
 724948.500491        5
 26709.402693         5
 44515.979952         5
 842445.709036        5
 187443.3

2018-08-12 22:07:44,388 logger 29 [INFO]    [make_npy]  0.000000e+00    19326
 inf                11
 3.861531e+03       10
 1.265622e+04       10
 1.265622e+04        9
 6.034865e+04        7
 4.080181e+04        7
 1.501235e+05        7
 3.738225e+03        7
 4.451598e+04        7
 2.670940e+04        6
 3.861531e+03        5
 4.451598e+04        5
 1.812117e+04        5
 7.361945e+04        5
 2.851521e+04        5
 1.898433e+04        5
 1.265622e+04        5
 2.394207e+04        5
 4.406682e+04        5
 4.288329e+04        5
 9.310688e+04        5
 2.670940e+04        5
 3.591341e+04        5
 3.066594e+04        5
 2.670940e+04        5
 1.501235e+05        4
 5.594888e+03        4
 7.710726e+03        4
 1.331288e+04        4
 3.615034e+04        4
 3.627161e+04        4
 3.239986e+04        4
 1.218788e+04        4
 1.460779e+05        4
 3.888644e+04        4
 6.034868e+04        4
 2.456762e+04        4
 3.888644e+04        4
 8.997941e+03        4
 4.420464e+04        4
 1

2018-08-12 22:09:56,243 logger 29 [INFO]    [make_npy]  0.000000    19326
 inf            11
 0.070312        4
 0.276746        3
 0.239999        3
 0.197847        3
 0.126734        3
 0.255683        3
 0.136133        3
 0.494669        2
 0.672435        2
 0.208855        2
 0.512276        2
 0.242871        2
 1.843918        2
 0.187833        2
 0.315002        2
 0.479684        2
 0.087000        2
 0.189070        2
 0.312191        2
 0.241616        2
 1.079399        2
 0.341613        2
 0.105612        2
 0.155338        2
 0.297889        2
 0.955954        2
 1.099649        2
 0.132729        2
 0.487105        2
 0.142450        2
 0.170798        2
 0.079609        2
 0.831068        2
 0.165955        2
 0.305011        2
 0.108986        2
 0.187500        2
 0.778689        2
 0.121034        2
 0.512127        2
 0.339983        2
 0.189970        2
 0.212435        2
 0.640674        2
 0.216995        2
 0.395459        2
 2.443807        2
 0.049729     

In [102]:
' 2段階の集計 '
df = data
level = [unique_id, p_id]
num_list = [col for col in df.columns if col.count('@')]

for method in method_list:
    method_list_2 = method_list.copy()
    if method in ['sum', 'max', 'min']:
        method_list_2.remove(method)
    for num in num_list:
        tmp = df.groupby(level)[num].agg({num:method}).reset_index().rename(columns={num:f'{num}_{method}@'})
    
        num_list_2 = [col for col in tmp.columns if col.count('@')]
        select_level_agg(base=base, data=tmp, ignore_list=ignore_features,  level=unique_id, method_list=method_list_2, num_list=num_list_2, prefix=prefix)

/mnt/c/Users/gixo/go/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:11: FutureWarning: using a dict on a Series for aggregation
is deprecated and will be removed in a future version
  # This is added back by InteractiveShellApp.init_path()
2018-08-12 22:10:00,740 logger 231 [INFO]    [select_level_agg] 
num: REMAING_PERIOD_DIFF@_sum@
method: mean
['SK_ID_CURR'] 
2018-08-12 22:10:00,740 logger 231 [INFO]    [select_level_agg] 
num: REMAING_PERIOD_DIFF@_sum@
method: mean
['SK_ID_CURR'] 
2018-08-12 22:10:00,740 logger 231 [INFO]    [select_level_agg] 
num: REMAING_PERIOD_DIFF@_sum@
method: mean
['SK_ID_CURR'] 
../../../github/module/feature_engineering.py:26: FutureWarning: using a dict on a Series for aggregation
is deprecated and will be removed in a future version
  result = df.groupby(level)[feature].agg({'tmp': {method}})
2018-08-12 22:10:00,869 logger 236 [INFO]    [select_level_agg] 
base: Index(['SK_ID_CURR'], dtype='object')
result: Index(['SK_ID_CURR', 'REMAING_PERI

2018-08-12 22:10:01,008 logger 231 [INFO]    [select_level_agg] 
num: REMAING_PERIOD_DIFF@_sum@
method: std
['SK_ID_CURR'] 
2018-08-12 22:10:01,008 logger 231 [INFO]    [select_level_agg] 
num: REMAING_PERIOD_DIFF@_sum@
method: std
['SK_ID_CURR'] 
2018-08-12 22:10:01,008 logger 231 [INFO]    [select_level_agg] 
num: REMAING_PERIOD_DIFF@_sum@
method: std
['SK_ID_CURR'] 
2018-08-12 22:10:01,113 logger 236 [INFO]    [select_level_agg] 
base: Index(['SK_ID_CURR'], dtype='object')
result: Index(['SK_ID_CURR', 'REMAING_PERIOD_DIFF@_sum@_std@['SK_ID_CURR']'], dtype='object') 
2018-08-12 22:10:01,113 logger 236 [INFO]    [select_level_agg] 
base: Index(['SK_ID_CURR'], dtype='object')
result: Index(['SK_ID_CURR', 'REMAING_PERIOD_DIFF@_sum@_std@['SK_ID_CURR']'], dtype='object') 
2018-08-12 22:10:01,113 logger 236 [INFO]    [select_level_agg] 
base: Index(['SK_ID_CURR'], dtype='object')
result: Index(['SK_ID_CURR', 'REMAING_PERIOD_DIFF@_sum@_std@['SK_ID_CURR']'], dtype='object') 
2018-08-12 22:10

2018-08-12 22:10:01,346 logger 236 [INFO]    [select_level_agg] 
base: Index(['SK_ID_CURR'], dtype='object')
result: Index(['SK_ID_CURR', 'REMAING_PERIOD_DIFF@_sum@_max@['SK_ID_CURR']'], dtype='object') 
2018-08-12 22:10:01,427 logger 239 [INFO]    [select_level_agg] 
result shape: (356255, 2) 
2018-08-12 22:10:01,427 logger 239 [INFO]    [select_level_agg] 
result shape: (356255, 2) 
2018-08-12 22:10:01,427 logger 239 [INFO]    [select_level_agg] 
result shape: (356255, 2) 
2018-08-12 22:10:01,442 logger 29 [INFO]    [make_npy] 66.0      36695
45.0      21596
15.0      18741
276.0      9299
153.0      5698
51.0       4197
65.0       4157
55.0       4064
63.0       3249
28.0       3104
0.0        2842
38.0       2712
60.0       2524
6.0        2461
56.0       2448
54.0       2275
30.0       2272
67.0       2268
91.0       2196
52.0       2086
14.0       2026
49.0       1847
34.0       1817
68.0       1718
69.0       1708
44.0       1669
75.0       1640
217.0      1625
198.0      1571
7

2018-08-12 22:10:01,650 logger 29 [INFO]    [make_npy] 0.0       62438
15.0      54732
45.0      26701
66.0      22747
6.0       11909
14.0       8888
10.0       7213
28.0       6524
9.0        4857
5.0        4186
30.0       4042
38.0       3739
51.0       3641
12.0       3627
55.0       3259
21.0       3235
65.0       3059
34.0       2823
11.0       2652
27.0       2607
63.0       2604
44.0       2301
19.0       2300
56.0       2284
16.0       2136
60.0       2105
42.0       2019
36.0       1972
17.0       1962
35.0       1940
54.0       1883
276.0      1828
52.0       1804
18.0       1758
153.0      1739
3.0        1694
7.0        1666
40.0       1627
49.0       1566
4.0        1486
22.0       1478
39.0       1427
33.0       1269
8.0        1186
20.0       1156
67.0       1095
46.0        994
26.0        917
24.0        810
68.0        808
          ...  
1585.0        1
1184.0        1
795.0         1
992.0         1
797.0         1
1332.0        1
880.0         1
824.0         1
1

2018-08-12 22:10:05,414 logger 29 [INFO]    [make_npy] -inf          34919
 0.000000      3073
-45.000000      986
-18.000000      955
-9.333333       748
 9.000000       677
 13.500000      597
-5.250000       593
 23.000000      588
 11.000000      502
 7.500000       482
-28.000000      457
 78.000000      446
 18.000000      442
 17.500000      417
-3.000000       408
-1.666667       404
 21.000000      403
 34.000000      400
-10.500000      392
 8.500000       386
 7.250000       379
 45.000000      376
-6.000000       376
 7.000000       369
 9.750000       369
 7.875000       355
 20.250000      346
 28.500000      345
-5.000000       328
 15.000000      325
 6.750000       325
 25.200000      316
 10.000000      316
 7.666667       315
 14.000000      305
 8.142857       304
 19.000000      303
 55.000000      292
 25.000000      286
 6.500000       273
 12.500000      272
 6.000000       267
 14.500000      265
-2.500000       263
 7.363636       262
-13.125000      258
-4.58

...

2018-08-12 22:13:22,131 logger 29 [INFO]    [make_npy] 0.000000     18
0.071878      2
0.100289      2
0.260109      2
1.009718      2
0.328397      2
0.508410      2
0.027121      2
0.374003      2
0.040006      2
0.050601      2
0.053740      2
0.096210      2
1.873188      2
0.063455      2
0.062404      2
0.041853      2
0.278986      2
0.254417      2
0.059953      2
0.091256      2
0.031440      2
0.385240      2
0.089790      2
0.066776      2
5.047323      2
0.031988      2
0.011013      2
0.614100      2
0.142411      2
0.102444      2
7.548198      2
1.180474      2
0.541904      2
1.771676      2
0.135915      2
0.143525      2
0.001163      2
0.128199      2
0.322613      2
0.256921      2
0.134204      2
0.073303      2
0.068776      2
0.149002      2
0.130429      2
0.070269      2
1.937629      2
0.047620      2
0.905831      2
             ..
1.212821      1
0.481365      1
1.540646      1
0.191793      1
0.041460      1
0.099282      1
0.556843      1
0.079576      1
0

2018-08-12 22:13:24,535 logger 231 [INFO]    [select_level_agg] 
num: REMAING_INS_AMT_INSTALMENT@_div_INCOME@_min@
method: sum
['SK_ID_CURR'] 
2018-08-12 22:13:24,535 logger 231 [INFO]    [select_level_agg] 
num: REMAING_INS_AMT_INSTALMENT@_div_INCOME@_min@
method: sum
['SK_ID_CURR'] 
2018-08-12 22:13:24,535 logger 231 [INFO]    [select_level_agg] 
num: REMAING_INS_AMT_INSTALMENT@_div_INCOME@_min@
method: sum
['SK_ID_CURR'] 
2018-08-12 22:13:24,642 logger 236 [INFO]    [select_level_agg] 
base: Index(['SK_ID_CURR'], dtype='object')
result: Index(['SK_ID_CURR', 'REMAING_INS_AMT_INSTALMENT@_div_INCOME@_min@_sum@['SK_ID_CURR']'], dtype='object') 
2018-08-12 22:13:24,642 logger 236 [INFO]    [select_level_agg] 
base: Index(['SK_ID_CURR'], dtype='object')
result: Index(['SK_ID_CURR', 'REMAING_INS_AMT_INSTALMENT@_div_INCOME@_min@_sum@['SK_ID_CURR']'], dtype='object') 
2018-08-12 22:13:24,642 logger 236 [INFO]    [select_level_agg] 
base: Index(['SK_ID_CURR'], dtype='object')
result: Index(['

2018-08-12 22:13:24,920 logger 239 [INFO]    [select_level_agg] 
result shape: (356255, 2) 
2018-08-12 22:13:24,954 logger 29 [INFO]    [make_npy]  0.000000     32
 0.100000     13
 inf          11
-0.452156      9
 0.166667      8
-0.452156      7
 0.200000      7
-0.753589      7
 0.125000      7
-0.055958      6
 0.133333      6
-0.301437      6
 0.083333      6
-0.542587      6
-3.000000      5
 0.175000      5
-0.100860      5
-0.100000      5
 0.050000      5
-0.175000      5
-0.084050      5
-0.200000      5
-0.778692      5
 0.033333      5
-1.073109      5
-0.025000      5
 0.085714      5
-0.249699      5
 0.128571      5
 0.057143      5
 0.225000      4
-0.266349      4
-1.800000      4
-1.750000      4
-3.850000      4
-0.399518      4
 0.040000      4
-0.066667      4
-0.074611      4
-0.252150      4
-0.325643      4
-0.516750      4
-0.140000      4
-0.361725      4
-0.060000      4
 0.400000      4
 0.240000      4
-1.600000      4
 0.180000      4
-0.166468      4
   

2018-08-12 22:13:25,177 logger 29 [INFO]    [make_npy] 0.000000     14
1.009718      2
0.508410      2
0.063455      2
0.113485      2
1.771676      2
0.143525      2
0.278986      2
0.087051      2
0.041853      2
0.433594      2
0.073303      2
0.173141      2
0.096210      2
0.031440      2
0.027121      2
0.905831      2
0.011013      2
0.875487      2
0.089790      2
0.260109      2
0.256921      2
0.075558      2
0.125775      2
0.142411      2
0.168201      2
7.548198      2
0.199575      2
0.622997      2
0.140086      2
0.064733      2
0.019240      2
0.033101      2
0.614100      2
0.117093      2
0.066776      2
0.541904      2
0.605082      2
0.241632      2
0.105257      2
0.100289      2
0.050601      2
0.352941      2
0.130429      2
0.173537      2
0.177421      2
0.141653      2
0.065870      2
0.047620      2
0.102225      2
             ..
0.749339      1
0.037333      1
0.500275      1
0.163197      1
0.149216      1
0.317736      1
0.081767      1
1.136973      1
0

2018-08-12 22:13:25,403 logger 29 [INFO]    [make_npy]  0.000000      98
 0.100000      42
 0.200000      25
 0.250000      23
 0.050000      22
 0.150000      19
 0.033333      18
 0.083333      18
 0.133333      17
 0.125000      17
 0.066667      16
 0.040000      16
 0.166667      15
 0.025000      15
 0.300000      15
 0.400000      14
 0.075000      14
 0.080000      13
 0.500000      12
-0.166468      12
-0.021632      12
 3.600000      12
 0.057143      12
-0.014421      12
 0.600000      12
-0.050000      11
 0.175000      11
 0.183333      11
 2.100000      11
 inf           11
 0.020000      11
-0.017306      11
 0.180000      11
 5.000000      10
-0.047022      10
-0.016667      10
 1.600000      10
 0.060000      10
 4.000000      10
 0.233333      10
-0.075000       9
-0.100000       9
-0.020940       9
 3.000000       9
 0.240000       9
 0.160000       9
-0.066667       9
 0.030000       9
-0.010816       9
-0.149221       9
               ..
 0.078574       1
-0.021472

In [103]:
' 重み付き平均と集計 '
data = df
level = [unique_id, p_id]
label = 'DAYS_INSTALMENT'
# label = 'DAYS_INSTALMENT@'
weight_list = [0.98]
feature_list = [col for col in df.columns if col.count('@')]

for num in feature_list:
    for weight in weight_list:
        wavg = exp_weight_avg(data=data, level=level, weight=weight, label=label, value=num)
        
        num_list = [wavg.name]
        wavg = wavg.to_frame().reset_index()
        select_level_agg(base=base, data=wavg, ignore_list=ignore_features, level=unique_id, method_list=method_list, num_list=num_list, prefix=prefix)

/mnt/c/Git/go/kaggle/kaggle_private/home-credit-default-risk/engineering/mv_wg_avg.py:85: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  null['weight'] = 0
2018-08-12 22:14:28,148 logger 231 [INFO]    [select_level_agg] 
num: REMAING_PERIOD_DIFF@_wg0.98_avg@['SK_ID_CURR', 'SK_ID_PREV']
method: sum
['SK_ID_CURR'] 
2018-08-12 22:14:28,148 logger 231 [INFO]    [select_level_agg] 
num: REMAING_PERIOD_DIFF@_wg0.98_avg@['SK_ID_CURR', 'SK_ID_PREV']
method: sum
['SK_ID_CURR'] 
2018-08-12 22:14:28,148 logger 231 [INFO]    [select_level_agg] 
num: REMAING_PERIOD_DIFF@_wg0.98_avg@['SK_ID_CURR', 'SK_ID_PREV']
method: sum
['SK_ID_CURR'] 
../../../github/module/feature_engineering.py:26: FutureWarning: using a dict on a Series for aggregation
is deprecated and will be removed i

2018-08-12 22:14:28,728 logger 231 [INFO]    [select_level_agg] 
num: REMAING_PERIOD_DIFF@_wg0.98_avg@['SK_ID_CURR', 'SK_ID_PREV']
method: mean
['SK_ID_CURR'] 
2018-08-12 22:14:28,728 logger 231 [INFO]    [select_level_agg] 
num: REMAING_PERIOD_DIFF@_wg0.98_avg@['SK_ID_CURR', 'SK_ID_PREV']
method: mean
['SK_ID_CURR'] 
2018-08-12 22:14:28,728 logger 231 [INFO]    [select_level_agg] 
num: REMAING_PERIOD_DIFF@_wg0.98_avg@['SK_ID_CURR', 'SK_ID_PREV']
method: mean
['SK_ID_CURR'] 
2018-08-12 22:14:28,816 logger 236 [INFO]    [select_level_agg] 
base: Index(['SK_ID_CURR'], dtype='object')
result: Index(['SK_ID_CURR', 'REMAING_PERIOD_DIFF@_wg0.98_avg@['SK_ID_CURR', 'SK_ID_PREV']_mean@['SK_ID_CURR']'], dtype='object') 
2018-08-12 22:14:28,816 logger 236 [INFO]    [select_level_agg] 
base: Index(['SK_ID_CURR'], dtype='object')
result: Index(['SK_ID_CURR', 'REMAING_PERIOD_DIFF@_wg0.98_avg@['SK_ID_CURR', 'SK_ID_PREV']_mean@['SK_ID_CURR']'], dtype='object') 
2018-08-12 22:14:28,816 logger 236 [INFO

2018-08-12 22:14:29,153 logger 236 [INFO]    [select_level_agg] 
base: Index(['SK_ID_CURR'], dtype='object')
result: Index(['SK_ID_CURR', 'REMAING_PERIOD_DIFF@_wg0.98_avg@['SK_ID_CURR', 'SK_ID_PREV']_std@['SK_ID_CURR']'], dtype='object') 
2018-08-12 22:14:29,242 logger 239 [INFO]    [select_level_agg] 
result shape: (356255, 2) 
2018-08-12 22:14:29,242 logger 239 [INFO]    [select_level_agg] 
result shape: (356255, 2) 
2018-08-12 22:14:29,242 logger 239 [INFO]    [select_level_agg] 
result shape: (356255, 2) 
2018-08-12 22:14:29,273 logger 29 [INFO]    [make_npy] 0.000000e+00    1650
8.881784e-16     345
1.992908e+00     322
1.338095e+00     313
4.440892e-16     283
6.280370e-16     262
1.256074e-15     247
6.548135e-01     198
1.992908e+00     184
6.548135e-01     174
1.992908e+00     156
1.338095e+00     147
6.548135e-01     138
7.071068e-01     138
6.548135e-01     134
3.666430e-01     115
1.414214e+00     113
3.666430e-01     102
1.627203e+00      99
4.242641e+00      99
4.242641e+

2018-08-12 22:14:29,397 logger 236 [INFO]    [select_level_agg] 
base: Index(['SK_ID_CURR'], dtype='object')
result: Index(['SK_ID_CURR', 'REMAING_PERIOD_DIFF@_wg0.98_avg@['SK_ID_CURR', 'SK_ID_PREV']_max@['SK_ID_CURR']'], dtype='object') 
2018-08-12 22:14:29,478 logger 239 [INFO]    [select_level_agg] 
result shape: (356255, 2) 
2018-08-12 22:14:29,478 logger 239 [INFO]    [select_level_agg] 
result shape: (356255, 2) 
2018-08-12 22:14:29,478 logger 239 [INFO]    [select_level_agg] 
result shape: (356255, 2) 
2018-08-12 22:14:29,503 logger 29 [INFO]    [make_npy] 5.259488     6889
5.259488     6760
4.333442     5751
2.441090     5154
5.259488     4778
4.333442     3945
2.441090     3877
2.441090     3161
5.798140     2725
9.474750     2558
8.474750     2530
8.441090     2473
9.474750     2288
8.441090     2165
5.798140     1861
8.959602     1822
10.535732    1819
5.333442     1802
2.959602     1748
10.535732    1706
10.000000    1687
11.000000    1660
6.393983     1650
6.333442     153

2018-08-12 22:14:29,711 logger 29 [INFO]    [make_npy] 2.441090     24896
2.441090     16574
2.441090     14136
4.333442     12705
5.259488     11113
4.333442     10687
5.259488      9406
2.959602      5855
5.259488      5719
1.474750      5342
1.474750      4455
2.959602      3557
3.474750      3195
2.959602      2945
5.798140      2828
3.393983      2818
3.393983      2642
3.474750      2630
2.077176      2207
4.865390      2115
4.865390      2074
1.959602      2020
5.259488      1981
4.333442      1972
5.798140      1964
1.474750      1897
2.474750      1678
2.441090      1634
4.798140      1586
8.441090      1575
5.333442      1509
5.000000      1498
6.333442      1445
2.077176      1333
8.441090      1324
6.333442      1240
4.333442      1195
3.986532      1190
9.474750      1173
4.494949      1165
6.865390      1156
6.393983      1134
2.229922      1131
3.474750      1109
5.865390      1106
3.393983      1070
3.986532      1065
8.474750      1052
5.393983      1040
8.959602      

...

Name: REMAING_AMT_INSTALMENT@_div_INCOME@_wg0.98_avg@['SK_ID_CURR', 'SK_ID_PREV']_min@['SK_ID_CURR'], Length: 334097, dtype: int64 
2018-08-12 22:24:46,949 logger 29 [INFO]    [make_npy]  0.028981    18
 0.093402    16
 0.034777    16
 0.143754    14
 0.034777    14
 0.024841    13
 0.017389    12
 0.021736    11
 0.151790    10
 0.024841    10
 0.140102     9
 0.019321     8
 0.115003     8
 0.112082     7
 0.043472     7
 0.080058     7
 0.092187     7
 0.161943     7
 0.160117     6
 0.140102     6
 0.156217     6
 0.129062     6
 0.080664     6
 0.071877     6
 0.112082     6
 0.161328     6
 0.161328     6
 0.126702     6
 0.028981     5
 0.168123     5
 0.126702     5
 0.186803     5
 0.028056     5
 0.107962     5
 0.033667     5
 0.017389     5
 0.021736     5
 0.028056     5
 0.033041     5
 0.210155     5
 0.092539     5
 0.042083     5
 0.028981     5
 0.193594     4
 0.186803     4
 0.168936     4
 0.035273     4
 0.093402     4
 0.187408     4
 0.078109     4
             

2018-08-12 22:25:51,782 logger 231 [INFO]    [select_level_agg] 
num: REMAING_INS_AMT_INSTALMENT@_div_INCOME@_wg0.98_avg@['SK_ID_CURR', 'SK_ID_PREV']
method: mean
['SK_ID_CURR'] 
2018-08-12 22:25:51,782 logger 231 [INFO]    [select_level_agg] 
num: REMAING_INS_AMT_INSTALMENT@_div_INCOME@_wg0.98_avg@['SK_ID_CURR', 'SK_ID_PREV']
method: mean
['SK_ID_CURR'] 
2018-08-12 22:25:51,782 logger 231 [INFO]    [select_level_agg] 
num: REMAING_INS_AMT_INSTALMENT@_div_INCOME@_wg0.98_avg@['SK_ID_CURR', 'SK_ID_PREV']
method: mean
['SK_ID_CURR'] 
2018-08-12 22:25:51,871 logger 236 [INFO]    [select_level_agg] 
base: Index(['SK_ID_CURR'], dtype='object')
result: Index(['SK_ID_CURR', 'REMAING_INS_AMT_INSTALMENT@_div_INCOME@_wg0.98_avg@['SK_ID_CURR', 'SK_ID_PREV']_mean@['SK_ID_CURR']'], dtype='object') 
2018-08-12 22:25:51,871 logger 236 [INFO]    [select_level_agg] 
base: Index(['SK_ID_CURR'], dtype='object')
result: Index(['SK_ID_CURR', 'REMAING_INS_AMT_INSTALMENT@_div_INCOME@_wg0.98_avg@['SK_ID_CURR',

2018-08-12 22:25:52,206 logger 239 [INFO]    [select_level_agg] 
result shape: (356255, 2) 
2018-08-12 22:25:52,206 logger 239 [INFO]    [select_level_agg] 
result shape: (356255, 2) 
2018-08-12 22:25:52,206 logger 239 [INFO]    [select_level_agg] 
result shape: (356255, 2) 
2018-08-12 22:25:52,239 logger 29 [INFO]    [make_npy] 0.000000      6
0.536397      2
0.965195      2
0.728829      2
0.546217      2
0.316464      2
0.047863      2
0.102313      2
0.243223      2
0.128572      2
0.693203      2
0.000200      2
0.480337      2
0.049788      2
2.553866      2
0.303934      2
0.247754      2
0.161693      2
0.433541      2
0.349979      2
0.002363      2
0.130838      2
0.207831      2
0.787353      2
0.012479      2
0.401292      2
0.098678      2
0.085196      2
0.303686      2
0.133292      2
1.511584      2
0.858015      2
1.333141      2
0.066688      2
0.651321      2
0.286076      2
0.996204      2
3.085715      2
0.317909      2
1.898514      2
0.144600      2
0.125551     

2018-08-12 22:25:52,489 logger 29 [INFO]    [make_npy] inf          11
0.562871      7
0.280207      6
0.143754      5
0.518505      5
0.302765      5
1.087882      4
2.465193      4
1.076057      4
1.426223      4
0.565018      4
0.704034      4
0.259513      4
0.131429      4
0.224164      4
0.140102      4
0.071877      4
0.426475      4
1.157240      4
0.500101      4
0.213238      4
0.215631      4
0.439618      3
0.273680      3
0.511013      3
0.323886      3
0.101687      3
0.210153      3
0.938118      3
1.248130      3
0.280207      3
3.051076      3
0.373063      3
0.346846      3
0.841885      3
1.167602      3
0.718966      3
0.248374      3
0.269905      3
0.161943      3
0.745302      3
0.659427      3
0.272878      3
0.607944      3
2.370737      3
0.622206      3
0.371879      3
2.226260      3
1.093031      3
1.078664      3
             ..
13.948051     1
0.555224      1
0.593856      1
0.162447      1
0.189810      1
53.410484     1
0.698286      1
0.280651      1
0

2018-08-12 22:25:52,803 logger 29 [INFO]    [make_npy]  0.000000    25
 0.028981    19
 0.034777    17
 0.093402    16
 0.034777    15
 0.017389    14
 0.143754    13
 0.024841    12
 0.021736    12
 0.140102    10
 0.024841    10
 0.151790     9
 0.115003     8
 0.140102     8
 0.019321     8
 0.161328     7
 0.126702     7
 0.080058     7
 0.043472     7
 0.112082     7
-0.005265     6
 0.028981     6
 0.156217     6
 0.160117     6
 0.126702     6
 0.129062     6
 0.112082     6
 0.161943     6
 0.080664     6
 0.071877     6
 0.210155     6
 0.071701     5
 0.224164     5
 0.101193     5
 0.033667     5
 0.161327     5
 0.186803     5
 0.168123     5
 0.028056     5
 0.019321     5
 0.092539     5
 0.028056     5
 0.017389     5
 0.175238     5
 0.107962     5
 0.046094     5
-0.004969     5
 0.101362     5
 0.092187     5
 0.033041     5
             ..
 0.058196     1
-0.081071     1
-2.038082     1
-0.001597     1
 0.056362     1
 0.034544     1
 0.778444     1
 0.034819     1
 